In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import pickle 
import numpy as np

In [3]:
with open("../Data/Emebeddings/embeddings_20ng_raw.pkl", "rb") as f:
    data_raw = pickle.load(f)

corpus = data_raw["corpus"]
embeddings = data_raw["embeddings"]

## Clustering and Dimensionality Reduction

In [4]:
from Clustering.Clustering import Clustering_and_DimRed
clustering = Clustering_and_DimRed(verbose = True, number_clusters_hdbscan = 20)
dim_red_embeddings, clusters, umap_mapper = clustering.cluster_and_reduce(embeddings)

c:\Users\arik_\anaconda3\envs\llm_sem\Lib\site-packages\umap\distances.py:1063: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
c:\Users\arik_\anaconda3\envs\llm_sem\Lib\site-packages\umap\distances.py:1071: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @numba.jit()
c:\Users\arik_\anaconda3\envs\llm_sem\Lib\site-packages\umap\distances.py:1086: NumbaD

UMAP(angular_rp_forest=True, metric='cosine', min_dist=0, n_components=5, random_state=42, verbose=True)
Sat Aug 19 13:30:10 2023 Construct fuzzy simplicial set
Sat Aug 19 13:30:11 2023 Finding Nearest Neighbors
Sat Aug 19 13:30:11 2023 Building RP forest with 12 trees
Sat Aug 19 13:30:19 2023 NN descent for 14 iterations
	 1  /  14
	 2  /  14
	 3  /  14
	 4  /  14
	 5  /  14
	 6  /  14
	Stopping threshold met -- exiting after 6 iterations
Sat Aug 19 13:30:55 2023 Finished Nearest Neighbor Search
Sat Aug 19 13:30:58 2023 Construct embedding


Epochs completed: 100%| ██████████ 200/200 [00:20]


Sat Aug 19 13:31:20 2023 Finished embedding


In [5]:
clustering.visualize_clusters_dynamic(embeddings, clusters, corpus)

## Extract Top Words

In [6]:
with open("../Data/Emebeddings/embeddings_20ng_vocab.pkl", "rb") as f:
    embeddings_vocab = pickle.load(f)

In [7]:
from ExtractTopWords import ExtractTopWords
extractor = ExtractTopWords.ExtractTopWords()

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\arik_\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\arik_\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [8]:
centroid_dict = extractor.extract_centroids(dim_red_embeddings, clusters)
vocab = extractor.compute_corpus_vocab(corpus, min_freq = 0.3, max_freq=0.9)

Processing corpus: 100%|██████████| 18466/18466 [00:33<00:00, 543.21it/s]


Most common words:
n't: 17117
would: 10872
one: 10144
people: 6442
like: 6409
get: 5815
know: 5742
also: 5589
use: 4989
think: 4981


In [9]:
words_per_topic = extractor.compute_words_topics(corpus, vocab, clusters)

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\arik_\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
Computing words per topic: 100%|██████████| 18466/18466 [00:19<00:00, 939.29it/s] 


In [10]:
tws, tfidfs = extractor.extract_topwords_tfidf(corpus, vocab, clusters, top_n_words=3000)


(20775, 20)


Computing word-topic matrix: 100%|██████████| 18466/18466 [00:42<00:00, 430.14it/s]
c:\Users\arik_\Documents\Dokumente\Studium\Master\LLM_seminar\Project\src\ExtractTopWords\ExtractTopWords.py:265: RuntimeWarning:

invalid value encountered in divide

c:\Users\arik_\Documents\Dokumente\Studium\Master\LLM_seminar\Project\src\ExtractTopWords\ExtractTopWords.py:266: RuntimeWarning:

divide by zero encountered in divide

c:\Users\arik_\Documents\Dokumente\Studium\Master\LLM_seminar\Project\src\ExtractTopWords\ExtractTopWords.py:268: RuntimeWarning:

invalid value encountered in multiply



In [11]:
len(np.unique(clusters))
len(vocab)

20775

In [12]:
output_tfidf = {
    "topics":np.array(list(tws.values())),
    "topic-word-matrix": np.ones((len(np.unique(clusters)) - 1 , len(vocab)))
}

In [13]:
for topic in tws.keys():
    print("Topic: ", topic)
    print("Topwords: ", tws[topic][:10])

Topic:  0
Topwords:  ['chopin.udel.edu', 'daredevil', 'prnt', 'h.a.r.d', 'goblin', 'shatterstar', 'nikon', 'deathlok', 'gre', 'tuner']
Topic:  1
Topwords:  ['xtappcontext', 'fbm', 'pixar', 'xtdisplay', 'xstuff', 'vogle', 'ftp.ncsa.uiuc.edu', 'raytracing', 'raytracer', 'hiview']
Topic:  2
Topwords:  ['gunshot', 'miyazawa', 'revolvers', 'semi-autos', 'kates', 'kleck', 'gnv.ifas.ufl.edu', 'rutledge', 'degan', 'gridlock']
Topic:  3
Topwords:  ['nkjz', 'uq\\', 'gizwt', 'qtct', 'kjr', 'm/-', 'nkh', 'pmfq', 'nux', 'bizw']
Topic:  4
Topwords:  ['passports', 'khojaly', 'hartill', 'aharonian', 'tarih', 'non-jewish', 'likud', 'babiali', 'defterleri', 'muratoff']
Topic:  5
Topwords:  ['kb/s', 'asante', 'cie', 'deskjets', 'daystar', 'master/slave', 'cisc', 'pli', 'multisession', 'quadras']
Topic:  6
Topwords:  ['theistic', 'unicorns', 'gay/bi', 'agnosticism', 'imams', 'queers', 'apostasy', 'charley', 'hadith', 'ontological']
Topic:  7
Topwords:  ['dickhead', 'bettman', 'smileys', 'retarded', 'narra

In [14]:
tws2, cosine_similarity= extractor.extract_topwords_centroid_similarity(vocab, embeddings_vocab, corpus, clusters, centroid_dict, umap_mapper, top_n_words = 3000)


Sat Aug 19 13:33:58 2023 Worst tree score: 0.35134842
Sat Aug 19 13:33:58 2023 Mean tree score: 0.36268457
Sat Aug 19 13:33:58 2023 Best tree score: 0.37967075
Sat Aug 19 13:34:02 2023 Forward diversification reduced edges from 276990 to 99863
Sat Aug 19 13:34:05 2023 Reverse diversification reduced edges from 99863 to 99863


c:\Users\arik_\anaconda3\envs\llm_sem\Lib\site-packages\scipy\sparse\_index.py:143: SparseEfficiencyWarning:

Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.



Sat Aug 19 13:34:08 2023 Degree pruning reduced edges from 114512 to 112287
Sat Aug 19 13:34:08 2023 Resorting data and graph based on tree order
Sat Aug 19 13:34:08 2023 Building and compiling search function


Epochs completed: 100%| ██████████ 30/30 [00:04]
Computing word-topic matrix: 100%|██████████| 18466/18466 [01:04<00:00, 285.27it/s]


In [15]:
output_cos = {
    "topics": np.array(list(tws2.values())),
    "topic-word-matrix": np.ones((len(np.unique(clusters)) - 1 , len(vocab)))
}

In [16]:
for topic in tws2.keys():
    print("Topic: ", topic)
    print("Topwords: ", tws2[topic][:10])

Topic:  0
Topwords:  ['chopin.udel.edu', 'goblin', 'daredevil', 'prnt', 'h.a.r.d', 'nikon', 'tuner', 'c/a', 'mjm', 'shatterstar']
Topic:  1
Topwords:  ['xtdisplay', 'xtappcontext', 'xapplresdir', 'raytracer', 'ray-tracing', 'xauth', 'xconfig', 'renderman', 'raytracing', 'ftp.ncsa.uiuc.edu']
Topic:  2
Topwords:  ['gunshot', 'miyazawa', 'b-d', 'judiciary', 'firepower', 'semi-autos', 'revolvers', 'kleck', 'kates', 'jsh']
Topic:  3
Topwords:  ['gizwt', 'm/-', 'uq\\', 'nkjz', 'qtct', 'nkh', 'kjr', 'pmfq', 'nux', 'bizw']
Topic:  4
Topwords:  ['non-jewish', 'aharonian', 'tarih', 'khojaly', 'passports', 'likud', 'hartill', 'intifada', 'muratoff', 'erevan']
Topic:  5
Topwords:  ['kb/s', 'deskjets', 'asante', 'controler', 'oscillators', 'infoworld', 'multisession', 'daystar', 'cisc', 'cie']
Topic:  6
Topwords:  ['theistic', 'telepathy', 'unicorns', 'gay/bi', 'apostasy', 'charley', 'agnosticism', 'imams', 'mow', 't.r.m']
Topic:  7
Topwords:  ['narrative', 'bettman', 'retarded', 'dickhead', 'smile

## Evaluation

In [17]:
import Evaluation.Metrics as metrics
from sentence_transformers import SentenceTransformer

In [18]:
emb_dict = metrics.Embed_vocab(vocab, embedder = SentenceTransformer("paraphrase-MiniLM-L6-v2"), emb_filename= "vocab_embedding_20ng_minilml6", emb_path = "../src/Evaluation/Embeddings/vocab_embedding_20ng_minilml6.pkl")

In [19]:
metrics_dict = {
    "embedding_coherence": metrics.Embedding_Coherence(corpus_dict = emb_dict), 
    "npmi": metrics.NPMI_coherence_gensim(corpus, vocab, coherence = "u_mass"),
    "cos_sim_acc": metrics.Embedding_Intruder_cos_sim_accuracy(corpus_dict = emb_dict),
    "embedding_diversity": metrics.Embedding_Topic_Diversity(corpus_dict = emb_dict)
}

In [20]:
metric_results_tfidf = {}
for k,v in metrics_dict.items():
    metric_results_tfidf[k] = v.score(output_tfidf)

100%|██████████| 20/20 [00:00<00:00, 22280.50it/s]


In [21]:
metric_results_cossim = {}
for k,v in metrics_dict.items():
    metric_results_cossim[k] = v.score(output_cos)

100%|██████████| 20/20 [00:00<?, ?it/s]


In [22]:
metric_results_tfidf

{'embedding_coherence': 0.18764406703412534,
 'npmi': -16.80427396943818,
 'cos_sim_acc': 0.31999999999999995,
 'embedding_diversity': 0.41874827213316235}

In [23]:
metric_results_cossim

{'embedding_coherence': 0.19256571792066096,
 'npmi': -17.03500737861625,
 'cos_sim_acc': 0.27499999999999997,
 'embedding_diversity': 0.39511206193964693}

## Topic description

In [74]:
import TopicRepresentation
import sys
sys.path.insert(0, '..') 
import src

In [75]:
with open("../Data/SavedTopicRepresentations/Topics_20ng_v1.pkl", "rb") as f:
    topics = pickle.load(f)

Sat Aug 19 14:09:50 2023 Building and compiling search function


In [76]:
import os
api_key_openai = os.environ.get('OPENAI_API_KEY')
org_openai = os.environ.get('OPENAI_ORG')

import openai
openai.organization = org_openai

In [77]:
from TopwordEnhancement.TopwordEnhancement import TopwordEnhancement
enhancer = TopwordEnhancement(openai_key = api_key_openai, openai_model= "gpt-3.5-turbo-16k", max_context_length = 16000, openai_model_temperature= 0.5)

In [78]:
topic = topics[2]
topwords = topic.top_words["tfidf"]
for w in topwords:
    print(w)

miyazawa
gunshot
gridlock
kleck
kates
jsh
semi-autos
libertarianism
kerosene
plutonium
degan
rutledge
t.p.g
fbi/batf
vessey
full-auto
b-d
socialized
firepower
revolvers
heroin
gnv.ifas.ufl.edu
felons
copayments
unsealed
loudspeakers
paxton
albright
pistols
kopel
hmo
malpractice
judiciary
arlen
unorganized
bentsen
glocks
semiautomatic
overturn
reverend
seige
doorbell
sniper
batf/fbi
assailant
assualt
protestors
tamu.edu
scripter
moynihan
trailers
ammendment
boiler
hostages
lantern
reactors
importation
jonestown
specter
u.s.c
legalization
restraining
municipal
advisors
cultists
turbine
multilateral
referendum
gunfire
shootings
rifleman
enact
marksmanship
atf/fbi
misfire
jrm
electorate
schumer
quigley
sawed-off
ffl
jfk
non-violent
iftccu
vietnamese
apocalypse
canisters
dividians
spectre
democracies
napalm
h.b
mubarak
deterrent
tenants
commando
rambo
ordinance
uva
wod
lanterns
blasting
pumped
usc
clancy
cescript
woodstove
jamestown
peaceably
nra-ila
reitman
metzenbaum
semper
cross-examinat

In [79]:
model_output = enhancer.describe_topic_topwords_str(topwords, n_words = 500)
print(model_output)

The common topic of the provided words appears to be "gun control" or "firearms". 

Aspects and sub-topics of this topic include:
1. Gun ownership: "semi-autos", "revolvers", "pistols", "rifles"
2. Gun regulations: "gun control", "legislation", "repealing"
3. Gun violence: "shootings", "gunfire", "shooters", "homicide"
4. Law enforcement: "FBI/BATF", "police", "marshal"
5. Political debate: "libertarianism", "democrat", "republican", "congressmen"


In [80]:
for topic in topics: 
    print("Topic: ", topic.topic_name)
    print("Topwords: ", topic.top_words["tfidf"][:20])
    description = enhancer.describe_topic_topwords_str(topic.top_words["tfidf"], n_words = 100)
    print("Description:")
    print(description)
    print("\n\n\n")

Topic:  Electronics devices.
Topwords:  ['chopin.udel.edu', 'prnt', 'goblin', 'h.a.r.d', 'daredevil', 'c/a', 'ampere', 'nikon', 'shatterstar', 'deathlok', 'thd', 'deadpool', 'gre', 'lead-acid', 'adcom', 'mjm', 'koutd', 'tuner', 'oversampling', 'polybagged']
Description:
The common topic of the given words appears to be "Electronics and Entertainment". 

Aspects and sub-topics of this topic include:
1. Electronics: prnt, ampere, nikon, tuner, voltometer, fuses, amplifiers, flyback
2. Audio equipment: adcom, dolby, polk, onkyo, audiophile
3. Entertainment: daredevil, goblin, shatterstar, deathlok, deadpool, warlock
4. Media: simpsons, cinema, cover/poster, camcorder, cameo
5. Miscellaneous: hams, fiberglass, bulbs, conductivity, relays




Topic:  Computer Graphics
Topwords:  ['xtdisplay', 'xtappcontext', 'visualisation', 'raytracer', 'hiview', 'raytracing', 'renderman', 'doit', 'pixar', 'renderers', 'lipman', 'ray-tracing', 'vogle', 'bbses', 'quantized', 'fbm', 'xcreatewindow', 'badmatc

In [81]:
len(topics[1].documents)

1114

In [82]:
enhancer.describe_topic_documents_completion_object(topics[2].documents)

Too many documents given. Using only the first part of the documents that fits into the context length. Number of documents used:  169


<OpenAIObject chat.completion id=chatcmpl-7pF6IjYlSKb5IBiBtTw017EaeSRSX at 0x1f8d5d92690> JSON: {
  "id": "chatcmpl-7pF6IjYlSKb5IBiBtTw017EaeSRSX",
  "object": "chat.completion",
  "created": 1692447130,
  "model": "gpt-3.5-turbo-16k-0613",
  "choices": [
    {
      "index": 0,
      "message": {
        "role": "assistant",
        "content": "Based on the provided documents, the common topic seems to be the Waco incident and the government's handling of the situation. Some sub-topics within this theme include criticism of the government's actions, calls for investigations, concerns about civil rights violations, discussions about the media's coverage of the event, and debates about gun control."
      },
      "finish_reason": "stop"
    }
  ],
  "usage": {
    "prompt_tokens": 16064,
    "completion_tokens": 66,
    "total_tokens": 16130
  }
}

## Topic-based Prompting

In [83]:
from TopicPrompting.TopicPrompting import TopicPrompting

In [84]:
data = pickle.load(open("../Data/Emebeddings/embeddings_20ng_raw.pkl", "rb"))
embeddings = data["embeddings"]
corpus = data["corpus"]
vocab_embeddings = pickle.load(open("../Data/Emebeddings/embeddings_20ng_vocab.pkl", "rb"))

In [85]:
enhancer = TopwordEnhancement(api_key_openai)

pmp = TopicPrompting(
    openai_prompting_model = "gpt-3.5-turbo-16k",
    max_context_length_promting = 16348,
    topic_lis = topics,
    openai_key = api_key_openai, 
    openai_model_temperature_prompting = 1,
    enhancer=enhancer,
    vocab_embeddings=vocab_embeddings
)

#### Topic 13

In [86]:
print(topics[13].top_words["tfidf"][:20])

['flybys', 'reboost', 'astrophysical', 'quasars', 'voyagers', 'baalke', 'phobos', 'thruster', 'isas', 'ejasa', 'grbs', 'edo', 'dwarf', 'cometary', 'acronyms', 'triton', 'ulysses', 'spacewalks', 'eva', 'grb']


In [87]:
pmp.prompt_knn_search(llm_query = "What information on Jupiter does topic 13 contain?")

{
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "knn_search",
    "arguments": "{\n  \"topic_index\": 13,\n  \"query\": \"Jupiter\"\n}"
  }
}
GPT wants to the call the function:  {
  "name": "knn_search",
  "arguments": "{\n  \"topic_index\": 13,\n  \"query\": \"Jupiter\"\n}"
}
[{'role': 'system', 'content': "You are a helpful assistant. \nYou are excellent at inferring information about topics discovered via topic modelling using information retrieval. \nYou summarize information intelligently. \nYou use the functions you are provided with if applicable.\nYou make sure that everything you output is strictly based on the provided text. If you cite documents, give their indices. \nYou always explicitly say if you don't find any useful information!\nYou only say that something is contained in the corpus if you are very sure about it! "}, {'role': 'user', 'content': 'What information on Jupiter does topic 13 contain?'}, <OpenAIObject at 0x1f906739250> JSON: {


(<OpenAIObject chat.completion id=chatcmpl-7pF6PgZmTKQZt6yxSf3vuYoQnEJV9 at 0x1f897156810> JSON: {
   "id": "chatcmpl-7pF6PgZmTKQZt6yxSf3vuYoQnEJV9",
   "object": "chat.completion",
   "created": 1692447137,
   "model": "gpt-3.5-turbo-16k-0613",
   "choices": [
     {
       "index": 0,
       "message": {
         "role": "assistant",
         "content": "Topic 13 contains information on Jupiter in the following documents:\n\n1. Document 73: This document is about our solar system and mentions Jupiter as one of the planets named after Roman deities.\n\n2. Document 82: This document discusses future missions and mentions the Galileo mission, which orbited Jupiter.\n\n3. Document 99: This document provides historical information on planetary probes and mentions the Mariner missions that explored Venus, Mars, and Mercury. It also mentions that Voyager missions provided detailed information about Jupiter.\n\n4. Document 41: This document includes a reference to painting the moon red and w

In [88]:
for line in topics[13].documents[82].split("."):
    print(line)

# >Coca Cola company will want to paint the moon red and white
  (Well, # >if not this moon, then a moon of Jupiter)


  This reminds me of the old Arthur C
 Clarke story about the Coca Cola ad stashed inside an experiment



In [89]:
pmp.prompt_knn_search(llm_query = "What information on Apollo 13 does topic 13 contain?")

{
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "knn_search",
    "arguments": "{\n  \"topic_index\": 13,\n  \"query\": \"Apollo 13\"\n}"
  }
}
GPT wants to the call the function:  {
  "name": "knn_search",
  "arguments": "{\n  \"topic_index\": 13,\n  \"query\": \"Apollo 13\"\n}"
}
[{'role': 'system', 'content': "You are a helpful assistant. \nYou are excellent at inferring information about topics discovered via topic modelling using information retrieval. \nYou summarize information intelligently. \nYou use the functions you are provided with if applicable.\nYou make sure that everything you output is strictly based on the provided text. If you cite documents, give their indices. \nYou always explicitly say if you don't find any useful information!\nYou only say that something is contained in the corpus if you are very sure about it! "}, {'role': 'user', 'content': 'What information on Apollo 13 does topic 13 contain?'}, <OpenAIObject at 0x1f9033afcb0> JS

(<OpenAIObject chat.completion id=chatcmpl-7pF6Y8OnwK38ILmqVbO7zF2MY0fZR at 0x1f8d5d93830> JSON: {
   "id": "chatcmpl-7pF6Y8OnwK38ILmqVbO7zF2MY0fZR",
   "object": "chat.completion",
   "created": 1692447146,
   "model": "gpt-3.5-turbo-16k-0613",
   "choices": [
     {
       "index": 0,
       "message": {
         "role": "assistant",
         "content": "Topic 13 contains information on Apollo 13. However, after searching the documents related to the topic, I found that none of them specifically mention Apollo 13."
       },
       "finish_reason": "stop"
     }
   ],
   "usage": {
     "prompt_tokens": 7552,
     "completion_tokens": 33,
     "total_tokens": 7585
   }
 },
 (['This file and other text and image files from JPL missions are available from the JPL Info public access computer site, reachable by Internet via anonymous ftp to pubinfo.jpl.nasa.gov (128.149.6.2); or by dialup modem to +1 (818) 354-1333, up to 9600 bits per second, parameters N-8-1. --------------------------

### Topic 9

In [90]:
print(topics[9].top_words["tfidf"][:20])

['t-bird', 'manta', 'invoice', 'synchros', 'corolla', 'understeer', 'oversteer', 'automatics', 'tach', 'knx', 'awd', 'pathfinder', 'downshift', 'fusi', 'caprice', 'tercel', 'suv', 'infiniti', 'caltrans', 'moonroof']


In [91]:
pmp.prompt_knn_search(llm_query = "What information on the Toyota Corolla does topic 9 contain")

{
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "knn_search",
    "arguments": "{\n  \"topic_index\": 9,\n  \"query\": \"Toyota Corolla\",\n  \"k\": 5\n}"
  }
}
GPT wants to the call the function:  {
  "name": "knn_search",
  "arguments": "{\n  \"topic_index\": 9,\n  \"query\": \"Toyota Corolla\",\n  \"k\": 5\n}"
}
[{'role': 'system', 'content': "You are a helpful assistant. \nYou are excellent at inferring information about topics discovered via topic modelling using information retrieval. \nYou summarize information intelligently. \nYou use the functions you are provided with if applicable.\nYou make sure that everything you output is strictly based on the provided text. If you cite documents, give their indices. \nYou always explicitly say if you don't find any useful information!\nYou only say that something is contained in the corpus if you are very sure about it! "}, {'role': 'user', 'content': 'What information on the Toyota Corolla does topic 9 cont

(<OpenAIObject chat.completion id=chatcmpl-7pF6cLbal2gLtz2EFvfBn8nXBTrNk at 0x1f90375ba10> JSON: {
   "id": "chatcmpl-7pF6cLbal2gLtz2EFvfBn8nXBTrNk",
   "object": "chat.completion",
   "created": 1692447150,
   "model": "gpt-3.5-turbo-16k-0613",
   "choices": [
     {
       "index": 0,
       "message": {
         "role": "assistant",
         "content": "Topic 9 contains information on the Toyota Corolla in the following documents:\n\n1. Document 274: It is an advertisement for a 1982 Blue Toyota Corolla/Tercel for sale. The car is described as a 1982 Toyota Corolla/Tercel 5-Speed with 125K miles. It has blue color, air conditioning/heat, AM/FM stereo, and has been well taken care of and maintained. The owner mentions that it is a tough car that can generally go above 200K miles.\n\n2. Document 287: This document is an advertisement for a 1988 Toyota Corolla FX. The car is described as having an AM/FM radio and being in good condition. The mileage is low at 28,000, and the seller is 

In [92]:
topics[9].documents[274]

"Hi:  I have a '82 Blue TOYOTA Corolla/Tercel for sale:  Reason for seeling this great little car is my new Celica.  Car Specifications:  1982 Toyota Corolla/Tercel 5-Speed 125K miles 2 Door Blue Air conditioning/Heat AM/FM stereo Well taken care off and maintained clean New Battery, Timing Belt, and fan belt.  Inspection sticker valid until 02/94 A tough car, generally go above 200K miles.  Make me an offer.  E-mail : reddy@ulysses.att.com phone  : (908) 582-3861 (Work)   (201) 635-3705 (Home)   Kishore Reddy"

In [93]:
pmp.prompt_knn_search(llm_query = "What information on cars does topic 9 contain?")

{
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "knn_search",
    "arguments": "{\n  \"topic_index\": 9,\n  \"query\": \"cars\",\n  \"k\": 5\n}"
  }
}
GPT wants to the call the function:  {
  "name": "knn_search",
  "arguments": "{\n  \"topic_index\": 9,\n  \"query\": \"cars\",\n  \"k\": 5\n}"
}
[{'role': 'system', 'content': "You are a helpful assistant. \nYou are excellent at inferring information about topics discovered via topic modelling using information retrieval. \nYou summarize information intelligently. \nYou use the functions you are provided with if applicable.\nYou make sure that everything you output is strictly based on the provided text. If you cite documents, give their indices. \nYou always explicitly say if you don't find any useful information!\nYou only say that something is contained in the corpus if you are very sure about it! "}, {'role': 'user', 'content': 'What information on cars does topic 9 contain?'}, <OpenAIObject at 0x1f8d95f

(<OpenAIObject chat.completion id=chatcmpl-7pF6pixlg1ejqNNDyA02YRz8aPpJz at 0x1f8d95f0770> JSON: {
   "id": "chatcmpl-7pF6pixlg1ejqNNDyA02YRz8aPpJz",
   "object": "chat.completion",
   "created": 1692447163,
   "model": "gpt-3.5-turbo-16k-0613",
   "choices": [
     {
       "index": 0,
       "message": {
         "role": "assistant",
         "content": "Topic 9 contains information on cars such as cup holders, cellular phones, vanity mirrors, ashtrays, fake convertible roofs, vinyl roofs, and gold trim. The topic also mentions specific car models like the Lexus ES300, GS300, SC300, Infiniti J30, Toyota Camry, Lexus LS400, SC400, Acura Legend, Infiniti Q45, Lincoln Mark VIII, and Dodge Viper. There is also a mention of a specific Toyota Camry available for sale. Additionally, the topic discusses the Land Cruiser, describing it as a \"cult car\" with a passionate and loyal following. Finally, there is a description of a 1976 BMW 530i, highlighting its features, maintenance record, rel

In [94]:
pmp.prompt_knn_search(llm_query = "What information on Bananas does topic 9 contain?")

{
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "knn_search",
    "arguments": "{\n  \"topic_index\": 9,\n  \"query\": \"Bananas\",\n  \"k\": 5\n}"
  }
}
GPT wants to the call the function:  {
  "name": "knn_search",
  "arguments": "{\n  \"topic_index\": 9,\n  \"query\": \"Bananas\",\n  \"k\": 5\n}"
}
[{'role': 'system', 'content': "You are a helpful assistant. \nYou are excellent at inferring information about topics discovered via topic modelling using information retrieval. \nYou summarize information intelligently. \nYou use the functions you are provided with if applicable.\nYou make sure that everything you output is strictly based on the provided text. If you cite documents, give their indices. \nYou always explicitly say if you don't find any useful information!\nYou only say that something is contained in the corpus if you are very sure about it! "}, {'role': 'user', 'content': 'What information on Bananas does topic 9 contain?'}, <OpenAIObject at 

(<OpenAIObject chat.completion id=chatcmpl-7pF6xXAMMdWlvaWRh5AljlXtlkE8M at 0x1f8973f23f0> JSON: {
   "id": "chatcmpl-7pF6xXAMMdWlvaWRh5AljlXtlkE8M",
   "object": "chat.completion",
   "created": 1692447171,
   "model": "gpt-3.5-turbo-16k-0613",
   "choices": [
     {
       "index": 0,
       "message": {
         "role": "assistant",
         "content": "Topic 9 does not contain any information on bananas. The top documents retrieved related to cup holders, cellular phones, vanity mirrors, convertible roofs, and gold trim. None of these documents contain any relevant information about bananas."
       },
       "finish_reason": "stop"
     }
   ],
   "usage": {
     "prompt_tokens": 461,
     "completion_tokens": 44,
     "total_tokens": 505
   }
 },
 (["Cup holders (driving is an importantant enough undertaking) Cellular phones and mobile fax machines (see above) Vanity mirrors on the driver's side. Ashtrays (smokers seem to think it's just fine to use the road) Fake convertible roo

In [95]:
pmp.prompt_knn_search(llm_query = "What documents in topic 9 are about bananas?")

{
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "knn_search",
    "arguments": "{\n  \"topic_index\": 9,\n  \"query\": \"bananas\",\n  \"k\": 5\n}"
  }
}
GPT wants to the call the function:  {
  "name": "knn_search",
  "arguments": "{\n  \"topic_index\": 9,\n  \"query\": \"bananas\",\n  \"k\": 5\n}"
}
[{'role': 'system', 'content': "You are a helpful assistant. \nYou are excellent at inferring information about topics discovered via topic modelling using information retrieval. \nYou summarize information intelligently. \nYou use the functions you are provided with if applicable.\nYou make sure that everything you output is strictly based on the provided text. If you cite documents, give their indices. \nYou always explicitly say if you don't find any useful information!\nYou only say that something is contained in the corpus if you are very sure about it! "}, {'role': 'user', 'content': 'What documents in topic 9 are about bananas?'}, <OpenAIObject at 0x1f8

(<OpenAIObject chat.completion id=chatcmpl-7pF71ObHzA9ZBek2F3IOemP6Yh94z at 0x1f8d95f0350> JSON: {
   "id": "chatcmpl-7pF71ObHzA9ZBek2F3IOemP6Yh94z",
   "object": "chat.completion",
   "created": 1692447175,
   "model": "gpt-3.5-turbo-16k-0613",
   "choices": [
     {
       "index": 0,
       "message": {
         "role": "assistant",
         "content": "I found some documents in topic 9 that mention bananas. Here are a few examples:\n\n1. Document 348: This document talks about cup holders in cars and mentions that \"Ashtrays (smokers seem to think it's just fine to use the road) Fake convertible roofs and vinyl roofs. Any gold trim.\" This may not directly mention bananas, but it talks about various features in cars, including ashtrays, which could be used for disposing of banana peels.\n\n2. Document 335: This document discusses the idea of carrying non-alcoholic drinks without spilling them in cars. It mentions cup holders and suggests getting a hands-free model for cellular phon

In [96]:
topics[9].documents[348]

"Cup holders (driving is an importantant enough undertaking) Cellular phones and mobile fax machines (see above) Vanity mirrors on the driver's side. Ashtrays (smokers seem to think it's just fine to use the road) Fake convertible roofs and vinyl roofs. Any gold trim. "

In [97]:
pmp.prompt_knn_search(llm_query = "Are there documents in topic 9 about Ferraris and Volkswagens together?")

{
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "knn_search",
    "arguments": "{\n  \"topic_index\": 9,\n  \"query\": \"Ferraris and Volkswagens\"\n}"
  }
}
GPT wants to the call the function:  {
  "name": "knn_search",
  "arguments": "{\n  \"topic_index\": 9,\n  \"query\": \"Ferraris and Volkswagens\"\n}"
}
[{'role': 'system', 'content': "You are a helpful assistant. \nYou are excellent at inferring information about topics discovered via topic modelling using information retrieval. \nYou summarize information intelligently. \nYou use the functions you are provided with if applicable.\nYou make sure that everything you output is strictly based on the provided text. If you cite documents, give their indices. \nYou always explicitly say if you don't find any useful information!\nYou only say that something is contained in the corpus if you are very sure about it! "}, {'role': 'user', 'content': 'Are there documents in topic 9 about Ferraris and Volkswagens 

(<OpenAIObject chat.completion id=chatcmpl-7pF79QDLrKlpkhgMnLTghtcVqRCLs at 0x1f8d95f0e30> JSON: {
   "id": "chatcmpl-7pF79QDLrKlpkhgMnLTghtcVqRCLs",
   "object": "chat.completion",
   "created": 1692447183,
   "model": "gpt-3.5-turbo-16k-0613",
   "choices": [
     {
       "index": 0,
       "message": {
         "role": "assistant",
         "content": "Yes, there are documents in topic 9 that mention both Ferraris and Volkswagens together. Here are some of the documents:\n\n1. Document 123: The document mentions various car models, including Ferraris and Volkswagens, in a discussion about different cars.\n\n2. Document 110: This document talks about the Delorean using the Peugot/Renault/Volvo V6 engine in a rear-engine configuration and the Bricklin using some American iron in a front-engine rear-drive configuration.\n\n3. Document 348: It discusses various features in cars, including cup holders, cellular phones, vanity mirrors, and fake convertible roofs. While it doesn't specifi

In [98]:
topics[9].documents[110]

"    The Delorean used the Peugot/Renault/Volvo V6 in a rear engine configuration. The Bricklin use some 'Merkin iron in a front engine/rear drive configuration. "

In [99]:
pmp.prompt_knn_search(llm_query = "Summarize all documents about Fords in topic 9")

{
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "knn_search",
    "arguments": "{\n  \"topic_index\": 9,\n  \"query\": \"Fords\",\n  \"k\": 5\n}"
  }
}
GPT wants to the call the function:  {
  "name": "knn_search",
  "arguments": "{\n  \"topic_index\": 9,\n  \"query\": \"Fords\",\n  \"k\": 5\n}"
}
[{'role': 'system', 'content': "You are a helpful assistant. \nYou are excellent at inferring information about topics discovered via topic modelling using information retrieval. \nYou summarize information intelligently. \nYou use the functions you are provided with if applicable.\nYou make sure that everything you output is strictly based on the provided text. If you cite documents, give their indices. \nYou always explicitly say if you don't find any useful information!\nYou only say that something is contained in the corpus if you are very sure about it! "}, {'role': 'user', 'content': 'Summarize all documents about Fords in topic 9'}, <OpenAIObject at 0x1f8d9

(<OpenAIObject chat.completion id=chatcmpl-7pF7HAO2VnxyzrTEasMIvfYmrcdvH at 0x1f8d95f1070> JSON: {
   "id": "chatcmpl-7pF7HAO2VnxyzrTEasMIvfYmrcdvH",
   "object": "chat.completion",
   "created": 1692447191,
   "model": "gpt-3.5-turbo-16k-0613",
   "choices": [
     {
       "index": 0,
       "message": {
         "role": "assistant",
         "content": "Here is a summary of the documents about Fords in topic 9:\n\n1. Document 104: The document mentions Bricklins, which were manufactured in the 70s with engines from Ford. They have a distinctive and unique design, with an encased front bumper. While they are not very common, there are usually about ten of them listed in Hemmings (Motor News).\n\n2. Document 242: This document refers to a car that had pushbuttons in the steering wheel hub to control the automatic transmission. Shifting into reverse while turning a corner caused the wires to short and was disconcerting.\n\n3. Document 131: The author expresses a preference for a 1939 L

## Test Topic splitting

In [100]:
pmp.show_topic_list()

Topic 0: Electronics devices.
Topic 1: Computer Graphics
Topic 2: Gun control.
Topic 3: Email Privacy and Security
Topic 4: Armenian Genocide
Topic 5: Computer Hardware and Accessories
Topic 6: LGBTQ+ Issues
Topic 7: Online Communication and Etiquette
Topic 8: Computer Hardware/Software Issues
Topic 9: Car Performance
Topic 10: Encryption and Security
Topic 11: Technology and Computing
Topic 12: Technology.
Topic 13: Space Exploration
Topic 14: Motorcycle Accessories
Topic 15: Computer Programming
Topic 16: Hockey Players.
Topic 17: Medical Treatments
Topic 18: Baseball Players
Topic 19: Religious Controversies



In [101]:
r1 = pmp.general_prompt("What subtopics does topic 6 have?")

{
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "split_topic_kmeans",
    "arguments": "{\n  \"topic_idx\": 6\n}"
  }
}
GPT wants to the call the function:  {
  "name": "split_topic_kmeans",
  "arguments": "{\n  \"topic_idx\": 6\n}"
}


Epochs completed: 100%| ██████████ 100/100 [00:00]
Epochs completed: 100%| ██████████ 100/100 [00:01]
Computing word-topic matrix: 100%|██████████| 434/434 [00:00<00:00, 668.23it/s]
Epochs completed: 100%| ██████████ 100/100 [00:00]
100%|██████████| 1/1 [00:07<00:00,  7.14s/it]
Epochs completed: 100%| ██████████ 100/100 [00:00]
Epochs completed: 100%| ██████████ 100/100 [00:00]
Computing word-topic matrix: 100%|██████████| 182/182 [00:00<00:00, 727.82it/s]
Epochs completed: 100%| ██████████ 100/100 [00:00]
100%|██████████| 1/1 [00:04<00:00,  4.58s/it]


[{'role': 'system', 'content': "You are a helpful assistant. \nYou are excellent at inferring information about topics discovered via topic modelling using information retrieval. \nYou summarize information intelligently. \nYou use the functions you are provided with if applicable.\nYou make sure that everything you output is strictly based on the provided text. If you cite documents, give their indices. \nYou always explicitly say if you don't find any useful information!\nYou only say that something is contained in the corpus if you are very sure about it! "}, {'role': 'user', 'content': 'What subtopics does topic 6 have?'}, <OpenAIObject at 0x1f8d95f11f0> JSON: {
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "split_topic_kmeans",
    "arguments": "{\n  \"topic_idx\": 6\n}"
  }
}, {'role': 'function', 'name': 'split_topic_kmeans', 'content': '{"new topics": [{"topic_idx": 21, "topic_name": "Religion and Belief.", "topic_description": "The common topic of 

In [108]:
print(r1[0]["choices"][0]["message"]["content"])

Topic 6 has two subtopics:

1. Religion and Belief: This subtopic is characterized by words such as "apostasy," "religous," "telepathy," "supernatural," "hadith," and "theistic." It includes aspects such as religious conversion and renunciation, metaphysical and supernatural phenomena, discussions of Islamic religious texts, negative behavior or actions, cultural ideas and genetic traits, belief in a God or gods, contradictory behavior or beliefs, red herrings or distractions, evidence-based claims or arguments, and perfection or lack of flaws.

2. Sexuality and Deviant Behavior: This subtopic is related to sexuality and sexual behavior. It is characterized by words such as "gay/bi," "queer," "bisexual," "molesters," "molest," "pedophilia," "deviant," "anti-discrimination," "bigots," "mating," "orgasm," "monogamous," and "norms." It includes aspects such as LGBTQ+ issues, sexual deviance and molestation, social attitudes and discrimination, sexual behaviors and preferences, and societa

In [104]:
pmp.topic_lis = r1[1]

In [110]:
pmp.show_topic_list()

Topic 0: Electronics devices.
Topic 1: Computer Graphics
Topic 2: Gun control.
Topic 3: Email Privacy and Security
Topic 4: Armenian Genocide
Topic 5: Computer Hardware and Accessories
Topic 7: Online Communication and Etiquette
Topic 8: Computer Hardware/Software Issues
Topic 9: Car Performance
Topic 10: Encryption and Security
Topic 11: Technology and Computing
Topic 12: Technology.
Topic 13: Space Exploration
Topic 14: Motorcycle Accessories
Topic 15: Computer Programming
Topic 16: Hockey Players.
Topic 17: Medical Treatments
Topic 18: Baseball Players
Topic 19: Religious Controversies
Topic 21: Religion and Belief.
Topic 22: Sexuality and Deviant Behavior



In [113]:
len(pmp.topic_lis)

21

In [115]:
r2 = pmp.general_prompt("Combine the topics 19 and 20 into one single topic")

{
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "combine_topics",
    "arguments": "{\n  \"topic_idx_lis\": [19, 20]\n}"
  }
}
GPT wants to the call the function:  {
  "name": "combine_topics",
  "arguments": "{\n  \"topic_idx_lis\": [19, 20]\n}"
}


Epochs completed: 100%| ██████████ 100/100 [00:00]
Epochs completed: 100%| ██████████ 100/100 [00:03]
Computing word-topic matrix: 100%|██████████| 616/616 [00:01<00:00, 371.26it/s]
Epochs completed: 100%| ██████████ 100/100 [00:00]
100%|██████████| 1/1 [00:02<00:00,  2.86s/it]


[{'role': 'system', 'content': "You are a helpful assistant. \nYou are excellent at inferring information about topics discovered via topic modelling using information retrieval. \nYou summarize information intelligently. \nYou use the functions you are provided with if applicable.\nYou make sure that everything you output is strictly based on the provided text. If you cite documents, give their indices. \nYou always explicitly say if you don't find any useful information!\nYou only say that something is contained in the corpus if you are very sure about it! "}, {'role': 'user', 'content': 'Combine the topics 19 and 20 into one single topic'}, <OpenAIObject at 0x1f8e0c1cbf0> JSON: {
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "combine_topics",
    "arguments": "{\n  \"topic_idx_lis\": [19, 20]\n}"
  }
}, {'role': 'function', 'name': 'combine_topics', 'content': '{"new topics": {"topic_idx": 22, "topic_name": "Controversial Social Issues", "topic_descripti

In [118]:
print(r2[0]["choices"][0]["message"]["content"])

I have combined topics 19 and 20 into a new topic called "Controversial Social Issues."

This new topic includes various aspects and sub-topics, such as:

1. Sexuality: It covers topics related to gay/bi, queer, bisexuality, molesters, and deviant behavior.
2. Religion: It includes discussions about apostasy, hadith, t.r.m, theistic beliefs, and creationism.
3. Psychology: This sub-topic involves discussions about telepathy, metaphysical concepts, behaviorists, pedophilia, and pedophiles.
4. Societal issues: It addresses societal issues like sexism, hypocrisy, discrimination, and non-Muslim-related topics.
5. Philosophical concepts: It covers concepts like subjectivism, objectivism, epistemology, relativism, and objectivist beliefs.

Please note that this is a summary of the combined topics based on the words and themes present in those topics.


In [119]:
pmp.topic_lis = r2[1]

In [120]:
pmp.topic_lis

[Topic: Electronics devices.,
 Topic: Computer Graphics,
 Topic: Gun control.,
 Topic: Email Privacy and Security,
 Topic: Armenian Genocide,
 Topic: Computer Hardware and Accessories,
 Topic: Online Communication and Etiquette,
 Topic: Computer Hardware/Software Issues,
 Topic: Car Performance,
 Topic: Encryption and Security,
 Topic: Technology and Computing,
 Topic: Technology.,
 Topic: Space Exploration,
 Topic: Motorcycle Accessories,
 Topic: Computer Programming,
 Topic: Hockey Players.,
 Topic: Medical Treatments,
 Topic: Baseball Players,
 Topic: Religious Controversies,
 Topic: Controversial Social Issues]

In [123]:
print(pmp.topic_lis[2].topic_description)

The common topic of the given words appears to be "gun control" or "firearms". 

Aspects and sub-topics of this topic include:
1. Gun laws: regulations, restrictions, permits, and background checks.
2. Types of firearms: semi-autos, revolvers, pistols, rifles.
3. Gun violence: shootings, fatalities, homicides, injuries.
4. Law enforcement: FBI, BATF, police, law enforcement agencies.
5. Political debates: libertarianism, Democrat, Republican, legislation.


In [126]:
r3 = pmp.general_prompt("Please split topic 2 into two subtopics based on the subtopics 'Gun laws' and 'Types of firearms'.")

{
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "split_topic_keywords",
    "arguments": "{\n  \"topic_idx\": 2,\n  \"keywords\": [\"Gun laws\", \"Types of firearms\"]\n}"
  }
}
GPT wants to the call the function:  {
  "name": "split_topic_keywords",
  "arguments": "{\n  \"topic_idx\": 2,\n  \"keywords\": [\"Gun laws\", \"Types of firearms\"]\n}"
}


Epochs completed: 100%| ██████████ 100/100 [00:00]
Epochs completed: 100%| ██████████ 100/100 [00:02]
Computing word-topic matrix: 100%|██████████| 1308/1308 [00:02<00:00, 501.71it/s]
Epochs completed: 100%| ██████████ 100/100 [00:01]
100%|██████████| 1/1 [00:02<00:00,  2.91s/it]
Epochs completed: 100%| ██████████ 100/100 [00:01]
Epochs completed: 100%| ██████████ 100/100 [00:00]
Computing word-topic matrix: 100%|██████████| 49/49 [00:00<00:00, 909.77it/s]
Epochs completed: 100%| ██████████ 100/100 [00:00]
100%|██████████| 1/1 [00:03<00:00,  3.26s/it]


[{'role': 'system', 'content': "You are a helpful assistant. \nYou are excellent at inferring information about topics discovered via topic modelling using information retrieval. \nYou summarize information intelligently. \nYou use the functions you are provided with if applicable.\nYou make sure that everything you output is strictly based on the provided text. If you cite documents, give their indices. \nYou always explicitly say if you don't find any useful information!\nYou only say that something is contained in the corpus if you are very sure about it! "}, {'role': 'user', 'content': "Please split topic 2 into two subtopics based on the subtopics 'Gun laws' and 'Types of firearms'."}, <OpenAIObject at 0x1f8c496d5b0> JSON: {
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "split_topic_keywords",
    "arguments": "{\n  \"topic_idx\": 2,\n  \"keywords\": [\"Gun laws\", \"Types of firearms\"]\n}"
  }
}, {'role': 'function', 'name': 'split_topic_keywords', '

In [127]:
print(r3[0]["choices"][0]["message"]["content"])

I have split topic 2 into two subtopics based on the subtopics 'Gun laws' and 'Types of firearms'.

The first subtopic is 'Gun Control'. This topic encompasses aspects such as gun violence (shootings, homicides, massacres), legislation (enactment, amendment, repeal), firearms (pistols, rifles, semiautomatic, revolvers), policy and regulations (gun control, buyback, confiscation), and public safety (defense, deterrence, law enforcement). 

The second subtopic is 'Firearms and Machinery'. This topic includes aspects such as types of firearms (semi-autos, revolvers, full-auto), firearm components (primers, safeties, triggers, barrels), ammunition (misfire, magnum, reload, projectile, primer), firearm maintenance (cleaning, erosion, jammed, holster), and safety concerns (non-lethal, negligent, wasteful, dangerous).

Please note that these subtopics have been determined using topic modelling techniques on the provided text.


In [128]:
pmp.topic_lis = r3[1]
print(pmp.topic_lis)

[Topic: Electronics devices.
, Topic: Computer Graphics
, Topic: Email Privacy and Security
, Topic: Armenian Genocide
, Topic: Computer Hardware and Accessories
, Topic: Online Communication and Etiquette
, Topic: Computer Hardware/Software Issues
, Topic: Car Performance
, Topic: Encryption and Security
, Topic: Technology and Computing
, Topic: Technology.
, Topic: Space Exploration
, Topic: Motorcycle Accessories
, Topic: Computer Programming
, Topic: Hockey Players.
, Topic: Medical Treatments
, Topic: Baseball Players
, Topic: Religious Controversies
, Topic: Controversial Social Issues
, Topic: Gun Control
, Topic: Firearms and Machinery.
]


In [130]:
r4 = pmp.general_prompt("Please create a new topic based on Isreal")

{
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "add_new_topic_keyword",
    "arguments": "{\n  \"keyword\": \"Israel\"\n}"
  }
}
GPT wants to the call the function:  {
  "name": "add_new_topic_keyword",
  "arguments": "{\n  \"keyword\": \"Israel\"\n}"
}


Epochs completed: 100%| ██████████ 100/100 [00:00]
Processing corpus: 100%|██████████| 11704/11704 [00:25<00:00, 454.72it/s]


Most common words:
n't: 11814
would: 7516
one: 6956
people: 4666
max: 4346
like: 4303
get: 4007
know: 3815
also: 3812
use: 3537


Epochs completed: 100%| ██████████ 100/100 [00:00]


(17038, 22)


Computing word-topic matrix: 100%|██████████| 11704/11704 [00:48<00:00, 242.62it/s]
c:\Users\arik_\Documents\Dokumente\Studium\Master\LLM_seminar\Project\src\ExtractTopWords\ExtractTopWords.py:265: RuntimeWarning:

invalid value encountered in divide

Epochs completed: 100%| ██████████ 30/30 [00:02]
100%|██████████| 22/22 [01:55<00:00,  5.25s/it]


[{'role': 'system', 'content': "You are a helpful assistant. \nYou are excellent at inferring information about topics discovered via topic modelling using information retrieval. \nYou summarize information intelligently. \nYou use the functions you are provided with if applicable.\nYou make sure that everything you output is strictly based on the provided text. If you cite documents, give their indices. \nYou always explicitly say if you don't find any useful information!\nYou only say that something is contained in the corpus if you are very sure about it! "}, {'role': 'user', 'content': 'Please create a new topic based on Isreal'}, <OpenAIObject at 0x1f94a12b950> JSON: {
  "role": "assistant",
  "content": null,
  "function_call": {
    "name": "add_new_topic_keyword",
    "arguments": "{\n  \"keyword\": \"Israel\"\n}"
  }
}, {'role': 'function', 'name': 'add_new_topic_keyword', 'content': '{"new topics": {"topic_idx": 0, "topic_name": "Israeli-Palestinian Conflict", "topic_descript

In [131]:
print(r4[0]["choices"][0]["message"]["content"])

The common topic associated with the keyword "Israel" appears to be the "Israeli-Palestinian Conflict." This topic encompasses a variety of sub-topics and aspects related to the conflict. Here are some of the aspects related to this topic:

1. Historical figures and organizations: The topic includes references to historical figures such as Ben-Gurion, Meir, Dayan, as well as organizations like Haganah, Lehi, and Likud.

2. Geographical locations: The topic contains references to various geographic locations such as Jaffa, Golan, Hebron, Jle, Ramallah, Tel Aviv, and the Galilee.

3. Political issues: The topic encompasses political issues related to the conflict, including discussions about the Diaspora, Intifada, Occupation, Annexation, Retaliation, and Concessions.

4. Ethnic and religious aspects: The topic explores ethnic and religious aspects related to the conflict, including references to non-Jewish communities, synagogues, the Muslim faith, the Quran, as well as Arab and Semitic

In [133]:
print(r4[1])

[Topic: Weapons and Technology
, Topic: Electronics and Gaming.
, Topic: Graphics Programming
, Topic: Cryptocurrency and Cypherpunks
, Topic: Armenian Genocide
, Topic: Computer Hardware
, Topic: Sports
, Topic: Computer Hardware and Software
, Topic: Car Features
, Topic: Encryption and Security
, Topic: Technology and Literature.
, Topic: Technology and Literature.
, Topic: Space Exploration.
, Topic: Motorcycle Accessories
, Topic: Technology and Literature.
, Topic: Hockey Players
, Topic: Medicine and Health.
, Topic: Baseball Players
, Topic: Religious Beliefs
, Topic: Religion and sexuality.
, Topic: Gun control
, Topic: Israeli-Palestinian Conflict
]
